In [1]:
%matplotlib ipympl 

#import sys
#sys.path.insert(1, '/project/f/fherwig/fherwig/PythonVirtual/NuGridPy')

import numpy as np
from matplotlib import pyplot as plt

from nugridpy import nugridse as nuse
from nugridpy import utils

import os
import sys
import contextlib
import pandas as pd

import h5py

from matplotlib import colors as mcolors
from matplotlib.ticker import MaxNLocator

from astropy import constants as const
from astropy import units as u

from IPython.display import display
import ipywidgets as widgets
import matplotlib.patches as patches

from collections import defaultdict

import warnings
warnings.filterwarnings('ignore')

from IPython.display import display
import ipywidgets as widgets
import matplotlib.patches as patches

# important feature!
from multizone import mppnp_reader
import multizone_plot as mzp

In [2]:
results = {"MLT": 
                   {"folders": ["0.00E+00", "7.95E+01", "7.95E+02", "7.95E+03"]},
              
              "PPM":
                   {"folders": ["0.00E+00", "7.95E+01", "7.95E+02", "7.95E+03"]},
              
              "PPM3":
                   {"folders": ["0.00E+00", "7.95E+01", "7.95E+02", "7.95E+03"]},

              "PPM10":
                  {"folders": ["0.00E+00", "7.95E+01", "7.95E+02", "7.95E+03"]},
             
              "PPM50":
                  {"folders": ["0.00E+00", "7.95E+01", "7.95E+02", "7.95E+03"]},
              
              "GOSH":
                  {"folders": ["gosh", "gosh_stronger", "partial_merger", "partial_merger_stronger"] }
              

}

In [3]:
for run in results.keys():
    res = []
    for ing in results[run]["folders"]:

        if run != 'GOSH':
            obj = mppnp_reader(initialpath = "/data/niagara_project/projects/ocmerger_issa2025/CONDITIONS/initial_abund.dat",
                                surfpath = f"/data/niagara_project/projects/ocmerger_issa2025/RUNS/{run}_RUNS/hif{ing}/H5_surf")
        else:
            obj = mppnp_reader(initialpath = "/data/niagara_project/projects/ocmerger_issa2025/CONDITIONS/initial_abund.dat",
                        surfpath = f"/data/niagara_project/projects/ocmerger_issa2025/RUNS/{run}_RUNS/{ing}/H5_surf")
            
        res.append(obj)
        
    results[run]['results'] = res

In [8]:
stables = np.array(results['MLT']['results'][0].all_stable_species)

stables[0] = 'n'

all_isotopes = results['MLT']['results'][0].all_isos

In [32]:
import re
from collections import defaultdict

def parse_iso(iso):
    iso = str(iso).strip()
    if iso == "n":              # neutron special case
        return "n", 1           # treat like element="n", mass=1
    m = re.match(r"([A-Za-z]+)-(\d+)", iso)
    if not m:
        raise ValueError(f"Could not parse isotope string: {iso}")
    return m.group(1), int(m.group(2))
def unstable_heavier(all_isos, stable_isos):
    # Find heaviest stable isotope per element
    max_stable = defaultdict(int)
    for iso in stable_isos:
        elem, A = parse_iso(iso)
        if A > max_stable[elem]:
            max_stable[elem] = A
    
    # Collect unstable heavier ones
    unstable = []
    for iso in all_isos:
        elem, A = parse_iso(iso)
        if A > max_stable.get(elem, -1) and iso not in stable_isos:
            unstable.append(iso)
    return unstable


unstables = np.array(unstable_heavier(all_isotopes, stables))[145:]
print(unstables)

['Zn-71' 'Zn-72' 'Zn-73' 'Zn-74' 'Zn-75' 'Zn-76' 'Ga-72' 'Ga-73' 'Ga-74'
 'Ga-75' 'Ga-76' 'Ga-77' 'Ga-78' 'Ga-79' 'Ge-77' 'Ge-78' 'Ge-79' 'Ge-80'
 'Ge-81' 'Ge-82' 'As-76' 'As-77' 'As-78' 'As-79' 'As-80' 'As-81' 'As-82'
 'As-83' 'As-84' 'Se-83' 'Se-84' 'Se-85' 'Se-86' 'Se-87' 'Br-82' 'Br-83'
 'Br-84' 'Br-85' 'Br-86' 'Br-87' 'Br-88' 'Br-89' 'Kr-87' 'Kr-88' 'Kr-89'
 'Kr-90' 'Kr-91' 'Rb-88' 'Rb-89' 'Rb-90' 'Rb-91' 'Rb-92' 'Rb-93' 'Sr-89'
 'Sr-90' 'Sr-91' 'Sr-92' 'Sr-93' 'Sr-94' 'Sr-95' 'Y-90' 'Y-91' 'Y-92'
 'Y-93' 'Y-94' 'Y-95' 'Y-96' 'Y-97' 'Y-98' 'Zr-97' 'Zr-98' 'Zr-99'
 'Zr-100' 'Nb-94' 'Nb-95' 'Nb-96' 'Nb-97' 'Nb-98' 'Nb-99' 'Nb-100'
 'Nb-101' 'Nb-102' 'Mo-101' 'Mo-102' 'Mo-103' 'Mo-104' 'Mo-105' 'Ru-105'
 'Ru-106' 'Ru-107' 'Ru-108' 'Ru-109' 'Ru-110' 'Ru-111' 'Rh-104' 'Rh-105'
 'Rh-106' 'Rh-107' 'Rh-108' 'Rh-109' 'Rh-110' 'Rh-111' 'Rh-112' 'Rh-113'
 'Pd-111' 'Pd-112' 'Pd-113' 'Pd-114' 'Pd-115' 'Pd-116' 'Pd-117' 'Ag-110'
 'Ag-111' 'Ag-112' 'Ag-113' 'Ag-114' 'Ag-115' 'Ag-116' 'Ag-117' 'A

In [39]:
for run in results.keys():
    
    res = []
    for k,ing in enumerate(results[run]['folders']):

        res.append( results[run]['results'][k].get('surf', 11000, unstables, decay=False)
        
    results[run]['unstables'] = res

ValueError: operands could not be broadcast together with shapes (341,) (228,) 

In [64]:
for run in results.keys():
    print(run)
    for k,ing in enumerate(results[run]['folders']):
        print(ing)
        interesting = unstables[np.where(results[run]['unstables'][k] > 1e-10)[0]]
        
        
        if interesting != []:
            OP = np.log10(results[run]['unstables'][k][np.where(results[run]['unstables'][k] > 1e-10)[0]] / results[run]['results'][k].get('initial', np.nan, interesting))
        
        
        print('\t', OP)
        
    print(' ')

MLT
0.00E+00
	 []
7.95E+01
	 [1.62372665 1.76118438 1.96021531 1.87676368 1.82883275 1.90930747]
7.95E+02
	 [2.8540583  2.38336326 2.91334327 2.86023757 2.56031538 2.73927083
 2.32350025 3.10160145 2.89839359 2.90256884 2.81676651 2.77135432
 2.84964195 2.87781635 2.81802768 2.82017662 2.71659319 2.79710823]
7.95E+03
	 [2.99283955 3.38331283 2.70209291 3.23981921 3.4467239  2.87453749
 3.10167617 2.67765418 3.42165297 3.22011396 3.21666082 3.12899524
 3.38511038 3.08682463 3.16203534 3.19470794 3.12936978 3.13213197
 3.08075373 3.02722453 3.25130081 3.10911361]
 
PPM
0.00E+00
	 []
7.95E+01
	 [1.63798375 1.77373627 1.96840417 1.88830419 1.83933964 1.92015678]
7.95E+02
	 [2.92620124 2.39732512 2.9187523  2.97708209 2.57334107 2.76924671
 2.34649987 3.10349455 2.90253296 2.91060368 2.82765017 2.7820706
 2.85987567 2.88264392 2.82988213 2.83134071 2.730931   2.80827603]
7.95E+03
	 [3.66537246 3.30743985 4.1473394  3.13756288 3.59937744 4.19933597
 3.23170149 3.53801058 3.30368894 3.7583939

In [58]:
pnuclei = [
    ['Mo-92', 'Mo-94'],
    ['Ru-96', 'Ru-98'], 
    ['Cd-106', 'Cd-108'],
    ['Sn-112', 'Sn-114', 'Sn-115'],
    ['Xe-124', 'Xe-126'],
    ['Ba-130', 'Ba-132'], 
    ['Ce-136', 'Ce-138'],
    ['Dy-156', 'Dy-158'], 
    ['Er-162', 'Er-164']
]

In [65]:
for run in results.keys():
    print(run)
    for k,ing in enumerate(results[run]['folders']):
        print(ing)
        
        pairies = []
        
        for pair in pnuclei:
            OP = np.log10(results[run]['results'][k].get('surf', 11000, pair) / results[run]['results'][k].get('initial', np.nan, pair))
            
            pairies.append( round(OP[-1] - OP[0],3))
        
        print('\t', pairies)
        
    print(' ')

MLT
0.00E+00
	 [-0.036, 0.008, -0.025, -0.843, 0.341, -0.522, -0.499, 0.222, 0.7]
7.95E+01
	 [0.293, 0.137, 0.15, 0.464, 0.487, -0.771, -0.525, 0.61, 0.923]
7.95E+02
	 [0.353, 0.185, 0.254, 0.738, 0.235, -0.772, -0.532, 0.602, 0.793]
7.95E+03
	 [0.42, 0.245, 0.4, 1.018, 0.311, -0.634, -0.505, 0.627, 0.483]
 
PPM
0.00E+00
	 [0.06, 0.098, 0.054, -0.904, 0.31, -0.59, -0.499, 0.197, 0.622]
7.95E+01
	 [0.51, 0.322, 0.338, 0.511, 0.412, -0.772, -0.459, 0.582, 0.834]
7.95E+02
	 [0.604, 0.398, 0.468, 0.883, 0.24, -0.742, -0.455, 0.578, 0.636]
7.95E+03
	 [0.777, 0.509, 0.656, 1.63, 0.611, -0.211, -0.261, 0.87, 0.04]
 
PPM3
0.00E+00
	 [-0.135, 0.013, -0.055, -1.503, 0.447, -0.842, -0.728, 0.116, 0.965]
7.95E+01
	 [0.302, 0.191, 0.19, -0.125, 0.488, -0.882, -0.611, 0.527, 1.025]
7.95E+02
	 [0.386, 0.264, 0.345, 0.539, 0.116, -0.855, -0.611, 0.494, 0.845]
7.95E+03
	 [0.768, 0.508, 0.752, 1.715, 0.676, -0.192, -0.302, 0.742, -0.063]
 
PPM10
0.00E+00
	 [-0.84, -0.249, -0.451, -2.167, 0.769, -1.155, 